In [1]:
import ast
import csv
import json

import numpy as np
import pandas as pd

import plotly
from plotly.offline import iplot, init_notebook_mode
import plotly.graph_objs as go
import plotly.express as px

pd.set_option('display.max_columns', None)

## Loading datasets

In [24]:
opendoar_df = pd.read_csv('../data/raw/openDoar.tsv', delimiter='\t',
                         converters={'subject': ast.literal_eval,
                                    'additional_name': ast.literal_eval,
                                    'opendoar_id': ast.literal_eval,
                                    'content_type': ast.literal_eval,
                                    'institution': ast.literal_eval
                                    })
opendoar_df.head()

openaire_id  opendoar_id  \
0  opendoar____::38b3eff8baf56627478ec76a704e9b52          101   
1  opendoar____::2b44928ae11fb9384c4cf38708677c48          115   
2  opendoar____::3416a75f4cea9109507cacd8e2f2aefc           41   
3  opendoar____::07e1cd7dca89a1678042477183b7ac3f          119   
4  opendoar____::d1f491a404d6854880943e5c3cd9ca25          129   

                                     repository_name additional_name  \
0                      utrecht university repository              []   
1  dspace at indian institute of management kozhi...   [dspace@iimk]   
2             caltech engineering and science online              []   
3                 dcu online research access service         [doras]   
4                            earth-prints repository              []   

                          repository_url  \
0            http://dspace.library.uu.nl   
1              http://dspace.iimk.ac.in/   
2  http://calteches.library.caltech.edu/   
3                   http://doras.dcu.ie/   
4           http://www.earth-prints.org/   

                                         description           type  \
0  this site is a university repository providing...  institutional   
1  this site is a subject based university reposi...  institutional   
2  the caltech archives holds approximately 220 c...  institutional   
3  this site is an institutional repository provi...  institutional   
4  a subject based repository providing open acce...   disciplinary   

           update_date           start_date  \
0  2021-04-16 15:22:03  2006-01-13 12:55:13   
1  2021-02-18 17:36:43  2006-01-04 11:54:34   
2  2021-02-18 17:36:28  2006-01-04 14:47:04   
3  2021-02-18 17:36:44  2006-01-04 11:15:19   
4  2021-04-19 08:28:38  2006-01-30 16:43:11   

                                             subject  \
0                                [multidisciplinary]   
1  [ecology and environment, social sciences gene...   
2  [biology and biochemistry, chemistry and chemi...   
3                                [multidisciplinary]   
4                     [earth and planetary sciences]   

                                        content_type  \
0  [journal_articles, conference_and_workshop_pap...   
1  [journal_articles, conference_and_workshop_pap...   
2  [journal_articles, conference_and_workshop_pap...   
3  [journal_articles, conference_and_workshop_pap...   
4  [journal_articles, conference_and_workshop_pap...   

                                         institution  metadata_policy  \
0  [[university of utrecht, [universiteit utrecht...             True   
1  [[indian institute of management kozhikode, [i...             True   
2  [[california institute of technology, [caltech...             True   
3  [[dublin city university, [dcu], ie, [], , htt...             True   
4  [[istituto nazionale di geofisica e vulcanolog...             True   

   data_policy  submission_policy  content_policy               software  \
0         True              False            True                dspace    
1         True               True            True             dspace 4.1   
2         True               True            True          eprints 3.1.3   
3         True               True            True          eprints 3.0.5   
4         True               True            True  dspace 5.8.1-snapshot   

     api  
0  true   
1  true   
2  true   
3  true   
4  true

In [25]:
opendoar_df.columns

Index(['openaire_id', 'opendoar_id', 'repository_name', 'additional_name',
       'repository_url', 'description', 'type', 'update_date', 'start_date',
       'subject', 'content_type', 'institution', 'metadata_policy',
       'data_policy', 'submission_policy', 'content_policy', 'software',
       'api'],
      dtype='object')

In [28]:
def empty_list_is_nan(cell):
    if isinstance(cell, list):
        return np.nan if len(cell) == 0 else cell
    else:
        return cell
    
opendoar_df = opendoar_df.applymap(empty_list_is_nan)

In [29]:
opendoar_df.describe(include='all')

openaire_id   opendoar_id  \
count                                             5707   5707.000000   
unique                                            5707           NaN   
top     opendoar____::3cf166c6b73f030b4f67eeaeba301103           NaN   
freq                                                 1           NaN   
mean                                               NaN   4008.118801   
std                                                NaN   2869.948770   
min                                                NaN      2.000000   
25%                                                NaN   1823.000000   
50%                                                NaN   3361.000000   
75%                                                NaN   5095.000000   
max                                                NaN  10175.000000   

                               repository_name additional_name  \
count                                     5707            2138   
unique                                    5670            2096   
top     hiroshima associated repository portal              []   
freq                                         3               4   
mean                                       NaN             NaN   
std                                        NaN             NaN   
min                                        NaN             NaN   
25%                                        NaN             NaN   
50%                                        NaN             NaN   
75%                                        NaN             NaN   
max                                        NaN             NaN   

                            repository_url  \
count                                 5707   
unique                                5670   
top     http://harp.lib.hiroshima-u.ac.jp/   
freq                                     3   
mean                                   NaN   
std                                    NaN   
min                                    NaN   
25%                                    NaN   
50%                                    NaN   
75%                                    NaN   
max                                    NaN   

                                              description           type  \
count                                                5425           5707   
unique                                               4622              4   
top     this site provides access to the research outp...  institutional   
freq                                                   95           5067   
mean                                                  NaN            NaN   
std                                                   NaN            NaN   
min                                                   NaN            NaN   
25%                                                   NaN            NaN   
50%                                                   NaN            NaN   
75%                                                   NaN            NaN   
max                                                   NaN            NaN   

                update_date           start_date              subject  \
count                  5707                 5707                 5542   
unique                 2501                 5538                  819   
top     2020-09-18 12:53:48  2020-09-18 12:53:48  [multidisciplinary]   
freq                     82                   82                 3212   
mean                    NaN                  NaN                  NaN   
std                     NaN                  NaN                  NaN   
min                     NaN                  NaN                  NaN   
25%                     NaN                  NaN                  NaN   
50%                     NaN                  NaN                  NaN   
75%                     NaN                  NaN                  NaN   
max                     NaN                  NaN                  NaN   

                      content_type  \
coun

In [30]:
opendoar_df.isna().sum()

openaire_id             0
opendoar_id             0
repository_name         0
additional_name      3569
repository_url          0
description           282
type                    0
update_date             0
start_date              0
subject               165
content_type          144
institution             0
metadata_policy         0
data_policy             0
submission_policy       0
content_policy          0
software                0
api                     0
dtype: int64